<a href="https://colab.research.google.com/github/nicolasle/Vicsek/blob/main/Vicsek.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [110]:
%%capture
import numpy as np
import matplotlib.pyplot as plt
from math import cos, sin, sqrt, pi, exp, atan2
from math import radians as rad
from math import degrees as deg
import matplotlib.animation as animation
# import matplotlib
from IPython.display import HTML
from ipywidgets import IntProgress
from IPython.display import display
import random

# matplotlib.rcParams['animation.embed_limit'] = 2**128

# PARAMETERS

n_frames=100

death_distance=sqrt(2)
distance=5

noise=30
realignement_speed=0
size=100
Np=100
NP=100

def PBCdist(coord1,coord2):
    dx = coord1[0] - coord2[0]
    if (abs(dx) > size*0.5):
        dx = size - dx
    dy = coord1[1] - coord2[1]
    if (abs(dy) > size*0.5):
        dy = size - dy
    dist = np.sqrt(dx**2 + dy**2)
    return dist

f = IntProgress(min=0, max=n_frames)



fig, ax = plt.subplots(figsize=(10,10))
prey=size*np.random.rand(2,Np)
pred=size*np.random.rand(2,NP)

p_dirs=360*np.random.rand(Np)
P_dirs=360*np.random.rand(NP)

p_speeds=np.abs(np.random.normal(size/100,size/500,Np))
P_speeds=np.abs(np.random.normal(size/100,size/500,Np))


new_prey=prey 
mean_p_dir=p_dirs
new_pred=pred
mean_P_dir=P_dirs

def animate(n):
    ax.clear()
    ax.set_xlim([0,size])
    ax.set_ylim([0,size])

    prey=new_prey
    p_dirs=mean_p_dir
    pred=new_pred
    P_dirs=mean_P_dir
      
    for i,dir in zip(range(len(prey[0])),p_dirs):
        ax.plot([prey[0][i],prey[0][i]+size/100*cos(rad(dir))], [prey[1][i],prey[1][i]+size/100*sin(rad(dir))], color='g')
    for i,dir in zip(range(len(pred[0])),P_dirs):
        ax.plot([pred[0][i],pred[0][i]+size/100*cos(rad(dir))], [pred[1][i],pred[1][i]+size/100*sin(rad(dir))], color='r')
        # circle=plt.Circle((pred[0][i], pred[1][i]), distance, color='b', fill=False)
        # ax.add_patch(circle)
    

    for i in range(len(prey[0])):                                               #Loop for prey-prey interactions
        NN=0
        N_dir=0
        for j in range(len(prey[0])):
            if (i==j):
                continue
            if (PBCdist(prey[:,i], prey[:,j])<=distance):
                NN=NN+1
                N_dir=N_dir+p_dirs[j]
            
        if (NN==0):
            mean_p_dir[i]=p_dirs[i]+random.uniform(-noise,noise)
        else:
            mean_p_dir[i]=(p_dirs[i]+(N_dir/NN-p_dirs[i])*exp(-realignement_speed/abs((N_dir/NN-p_dirs[i])))+random.uniform(-noise,noise))%360
    
    to_kill=np.array([], int)
    for i in range(len(prey[0])):                                               #Loop for pred-prey interactions
        NN=0
        N_pred=np.empty((0,2))
        for j in range(len(pred[0])):
            if (PBCdist(prey[:,i], pred[:,j])<=death_distance):
                # to_kill=np.append(to_kill,i)
                ax.scatter(prey[0,i], prey[1,i], color='b')
                # circle=plt.Circle((pred[0][j], pred[1][j]), death_distance, color='b', fill=False)
                # ax.add_patch(circle)
            if (PBCdist(prey[:,i], pred[:,j])<=distance):
                NN=NN+1
                N_pred=np.append(N_pred, [pred[:,j]], axis=0)
        if (NN!=0):
            center_x=0
            center_y=0
            for x,y in zip(N_pred[:,0], N_pred[:,1]):
                center_x+=x
                center_y+=y
            center_x = center_x/NN
            center_y = center_y/NN
            dx=prey[0,i]-center_x
            dy=prey[1,i]-center_y
            angle=deg(atan2(dy,dx))%360
            mean_p_dir[i]=angle
            # ax.scatter(prey[0,i], prey[1,i], color='b')
    # prey=np.delete(prey, to_kill, axis=1)
         
            
    for i in range(len(prey[0])):
        new_prey[0][i]=(prey[0][i]+p_speeds[i]*cos(rad(mean_p_dir[i])))%size
        new_prey[1][i]=(prey[1][i]+p_speeds[i]*sin(rad(mean_p_dir[i])))%size
    for i in range(len(pred[0])):
        new_pred[0][i]=(pred[0][i]+P_speeds[i]*cos(rad(P_dirs[i])))%size
        new_pred[1][i]=(pred[1][i]+P_speeds[i]*sin(rad(P_dirs[i])))%size
    f.value += 1


ani=animation.FuncAnimation(fig, animate, interval=41.667, frames=n_frames)

In [111]:
f.value=0
display(f)
HTML(ani.to_jshtml())

IntProgress(value=0)